**Gojob**

In [4]:
# package manipulation des données 
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pandas_explode
pandas_explode.patch()
 
# package modélisation
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.cluster.bicluster import SpectralCoclustering
from sklearn.feature_extraction.text import CountVectorizer,TfidfVectorizer

#librairies pour les graphiques 
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

init_notebook_mode(connected=True)

**Telechargement de données**

In [14]:
data = pd.read_csv("worker_profession.csv")

In [15]:
# Affichage aléatoire de 5 éléments de la base
data.sample(5, random_state=42)

worker_id  \
21666  11eaa711-abba-4c62-848f-0574ca29b1e2   
3844   53af50ac-d894-4f98-89d5-95970cdb6f4a   
7932   29df22ff-a24e-405f-9463-81e8cca51eb9   
4702   0834dab8-17c8-4bd1-9928-99fd7fa9be4e   
13351  d510a165-2a4d-4eee-9081-5786525f25a3   

                                        list_professions  
21666  Employé contact clientèle |0;Opérateur de fabr...  
3844   Employé contact clientèle |0;Agent de conditio...  
7932   Agent d'entretien |2;Plongeur |0;Manutentionna...  
4702   Ouvrier d'exécution en milieu difficile |0;Com...  
13351  Préparateur de commandes |21;Ouvrier d'exécuti...

In [16]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 28448 entries, 0 to 28447
Data columns (total 2 columns):
worker_id           28448 non-null object
list_professions    28444 non-null object
dtypes: object(2)
memory usage: 444.6+ KB


In [17]:
data.isna().sum()

worker_id           0
list_professions    4
dtype: int64

In [18]:
data[data.list_professions.isna()]

worker_id list_professions
15417  4da26848-b5df-4f6c-b702-fe58e5d06ab9              NaN
17955  dbfa02f5-9b76-46a7-b39d-563d61ed168e              NaN
21924  05d645f1-5406-49ce-8da7-604940125113              NaN
23431  d7afab4f-b53d-431a-81cc-4e21ba3fabf8              NaN

In [19]:
data.dropna(inplace=True)

In [20]:
# les 4 éléments ont bien été supprimé
data.shape

(28444, 2)

In [23]:
# pas de répétition des ID
data.worker_id.is_unique

True

La liste de profession de trois individus au hasard

In [25]:
data.list_professions.sample(3,random_state=42).tolist()

["Employé de bureau |0;Employé contact clientèle |0;Ouvrier d'exécution polyvalent |0;Ouvrier d'exécution en milieu difficile |0",
 'Manoeuvre |0;Manutentionnaire |7;Couvreur |8;Menuisier |4',
 "Employé contact clientèle |0;Formation et carrière |200;Assistant polyvalent / Secrétaire |0;Ouvrier d'exécution polyvalent |0;Employé de bureau |0;Ouvrier d'exécution en milieu difficile |0"]

## 2. Analyse de données 

In [49]:
def clean_profession(p):
    cleaned_profession=p.split(";")
    for i in range(len(cleaned_profession)):
        cleaned_profession[i]=cleaned_profession[i].split(' |')
        cleaned_profession[i][0]=cleaned_profession[i][0].replace(' ','_')
        cleaned_profession[i][1]=int(cleaned_profession[i][1])
    return(cleaned_profession)

In [69]:
# nouveau format des données 
data1 = data.copy()
data1.list_professions = data1.list_professions.apply(clean_profession)
data1=data1.explode("list_professions")
data1["profession"]=data1.list_professions.apply(lambda r: r[0])
data1["nb_mois_xp"]=data1.list_professions.apply(lambda r: r[1])
data1.drop("list_professions",axis=1,inplace=True)
data1.head()

worker_id                 profession  nb_mois_xp
0  52754c03-3853-485b-8cc2-95c53684675c                Electricien           1
0  52754c03-3853-485b-8cc2-95c53684675c                    Cariste         107
0  52754c03-3853-485b-8cc2-95c53684675c  Employé_contact_clientèle           0
0  52754c03-3853-485b-8cc2-95c53684675c                 Commercial           1
0  52754c03-3853-485b-8cc2-95c53684675c                  Animation          27

 **Quelques statistiques**

Nous considérons que les individus avec une expérience de 0 n'ont jamais pu travailler dans ce domaine

In [74]:
(data1.nb_mois_xp > 0).mean()

0.256668927668496

In [75]:
data1 = data1[data1.nb_mois_xp > 0]

In [79]:
 data1.profession.nunique(),data1.worker_id.nunique()

(174, 23923)

Nous remarquons donc qu'il y'a des individus dans la base de donnée qui n'avaient jamais travaillé

In [108]:
def plot_bar(series,top_N=10):
    series = series[::-1][-top_N-1:]
    to_plot = [go.Bar(
               x = series.values,
               y = series.index,
               orientation = 'h'
    )]
    
    iplot(to_plot)

In [109]:
plot_bar(data1.groupby('profession').agg(sum).sort_values("nb_mois_xp", ascending=False).squeeze())

In [111]:
plot_bar(data1.groupby('profession').agg('mean').sort_values("nb_mois_xp", ascending=False).squeeze())

In [112]:
plot_bar(data1.profession.value_counts())

In [113]:
data1[data1.profession == "Préparateur_de_commandes"].nb_mois_xp.mean()

16.068130515083112

**Clustering**

**preparation des données**

In [115]:
data2= data1.groupby('worker_id').agg({'profession':lambda r: ' '.join(list(r))}).copy()

In [119]:
data2.head()

profession
worker_id                                                                              
0003e59c-a459-4842-b0ec-67a996c9f2fc                                            Vendeur
00043d14-f02b-4396-98c3-1783eaec6335                                  Employé_de_caisse
00053bba-f458-4d64-aa73-067ccfc88b1e                                            Cariste
00066800-1bea-4685-b475-61a63f0ebbba  Téléprospecteur Assistant_polyvalent_/_Secrétaire
000773d1-62f3-446f-be4b-b7bbc7627a54       Hôtesse Vendeur Artistique Employé_de_caisse

**Remarque**

Dans la plupart des exemples de sklearn, ils utilisent random_state=42.Mais cela ne devrait pas poser de problème. Puisque le random_state sert uniquement à recevoir les mêmes valeurs totales.C'est-à-dire, qu'en définissant un integer à random_state, celui-ci garantiras, que la même séquence de nombres aléatoires est générée chaque fois qu'on exécute le code.

Normalement on s'en sert lorsque l'on veux que les résultats soient toujours les mêmes. (En mode TEST/DEVELOPPEMENT)
En mode production, on ne veux justement pas, recevoir les mêmes résultats, donc on enlève le random_state.

In [124]:
data2.sample(4,random_state=1)

profession
worker_id                                                                              
cb4b279d-687d-472c-895a-48c057490cd5                                   Manutentionnaire
f339cd52-37d7-4047-83a2-77a63218a6ce  Préparateur_de_commandes Chauffeur_VL Agent_de...
5bf2cfdf-cf51-4c03-bc10-0c493503c925  Vendeur Commercial Opérateur_de_fabrication Pl...
c2dc66ac-cef8-4e8f-a1fa-06f5c71074cd                                            Cariste

voila à quoi ressemble l'association de chaque document à l'ensemble des tokens retenus pour ce dernier. Nous créons enfin la 
liste "docs" de l'ensemble des documents.

In [128]:
docs=data2.profession.tolist()
len(docs)

23923

**Une approche traditionnelle:KMeans**

**Une matrice binaire:Le countVectorizer**

In [234]:
counter= CountVectorizer()

In [235]:
sparse_data = counter.fit_transform(docs)
sparse_data

<23923x193 sparse matrix of type '<class 'numpy.int64'>'
	with 46790 stored elements in Compressed Sparse Row format>

In [134]:
#counter.get_feature_names()

['_fraiseur',
 '_international',
 '_médicale',
 '_projeteur',
 '_promotion',
 '_secrétaire',
 '_sécurité',
 '_technicienne_paie',
 'accompagnant_éducatif_et_social',
 'accompagnateur',
 'accueil',
 'acheteur',
 'administration_des_ventes',
 'affaires',
 'affrètement',
 'agent_d',
 'agent_de_conditionnement',
 'agent_de_distribution',
 'agent_de_nettoyage',
 'agent_de_recouvrement',
 'agent_de_service_hospitalier',
 'agent_de_transit',
 'aide_soignant',
 'ambulancier',
 'analyse_biomédicale',
 'animateur_de_ventes_',
 'animation',
 'animatrice_d',
 'approvisionneur',
 'artistique',
 'assistant_comptable',
 'assistant_de_direction',
 'assistant_de_service_social',
 'assistant_polyvalent_',
 'assitante_dentaire',
 'atelier',
 'audit',
 'auditeur_comptable',
 'auxiliaire_de_vie_sociale',
 'auxiliaire_puériculture',
 'avocat',
 'bobinier',
 'brancardier',
 'bureau_d',
 'cariste',
 'carreleur',
 'carrossier',
 'chargé_d',
 'chargé_de_clientèle',
 'charpentier',
 'chaudronnier',
 'chauffeur_p

In [236]:
sparse_data.toarray()

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 1, 0, 0]], dtype=int64)

In [214]:
def plot_line(x,y):
    fig = go.Figure(data=go.Scatter(x=x, y=y))
    fig.show()

In [215]:
sse = [KMeans(n_clusters=k,random_state=0).fit(sparse_data).inertia_ for k in range (2,10)]
plot_line(np.arange(2,10),sse)

In [237]:
kmeans = KMeans(n_clusters=6,random_state=0).fit(sparse_data)

In [238]:
pca = PCA(n_components=2).fit(sparse_data.toarray())

In [239]:
pca.explained_variance_ratio_

array([0.10132274, 0.08393464])

In [241]:
pca_components = pca.transform(sparse_data.toarray())

In [242]:
pca_components

array([[ 0.52629806, -0.62846094],
       [ 0.08394286,  0.09662194],
       [-0.09304225,  0.20779408],
       ...,
       [-0.8308889 , -0.19356116],
       [ 0.00971891,  0.15004902],
       [ 0.0086624 ,  0.15611901]])

In [243]:
cluster_df = pd.DataFrame(pca_components, columns=["C1","C2"])
cluster_df["cluster"] = kmeans.labels_
cluster_df.head()

C1        C2  cluster
0  0.526298 -0.628461        2
1  0.083943  0.096622        1
2 -0.093042  0.207794        5
3  0.424193  0.883650        4
4  0.622689 -0.678313        2

In [244]:
fig = px.scatter(cluster_df, x="C1", y="C2", color="cluster" )
fig.show()

In [247]:
#affichage des observations et leurs groupes
idk = np.argsort(kmeans.labels_)
data_cluster = pd.DataFrame({"worker_id" : data2.index[idk], "classes" : kmeans.labels_[idk]}) #"profession":data2.profession[idk]})

In [248]:
data_cluster.head()

worker_id  classes
0  6c539734-1a6a-4be3-af5a-7a91ecb6c20f        0
1  8d21526a-3b2d-41cd-8584-c241da8ed782        0
2  47fcf3e6-a6be-4af0-a7ad-bf05968426ae        0
3  d18567c4-aaad-45c4-9400-dc95e6f3efcb        0
4  3aff7e83-d9f0-469a-83a9-ee62b543e84f        0

In [249]:
data_cluster_prof = data2.groupby(kmeans.labels_).agg(sum).sort_values("profession", ascending=False)
data_cluster_prof

profession
2  VendeurHôtesse Vendeur Artistique Employé_de_c...
4  Téléprospecteur Assistant_polyvalent_/_Secréta...
3  Préparateur_de_commandes Plombier ManoeuvrePré...
1  Employé_de_caisseHôte_d'accueil Gestionnaire_d...
0  CommercialCommercial Chargé_de_clientèleCommer...
5  CaristeCaristeCariste Manoeuvre Commis_de_cuis...

In [250]:
# effectifs conditionnels
data2.groupby(kmeans.labels_).count()

profession
0        1772
1       10855
2        3861
3        4201
4        1789
5        1445

**TFIDF**

In [251]:
tfidf = TfidfVectorizer()
sparse_data_tf = tfidf.fit_transform(docs)
sparse_data_tf

<23923x193 sparse matrix of type '<class 'numpy.float64'>'
	with 46790 stored elements in Compressed Sparse Row format>

In [253]:
kmeans_tf = KMeans(n_clusters=6,random_state=0).fit(sparse_data_tf)
pca_tf = PCA(n_components=2).fit(sparse_data_tf.toarray())
pca_tf.explained_variance_ratio_

array([0.10501705, 0.079491  ])

In [255]:
pca_components_tf = pca_tf.transform(sparse_data_tf.toarray())
pca_components_tf

array([[-0.43468075,  0.77438633],
       [-0.11229917, -0.09633967],
       [-0.05733747, -0.37487237],
       ...,
       [ 0.26893808, -0.02063859],
       [-0.06881497, -0.11234424],
       [-0.06990025, -0.11520824]])

In [256]:
cluster_df_tf = pd.DataFrame(pca_components_tf, columns=["C1","C2"])
cluster_df_tf["cluster"] = kmeans_tf.labels_
cluster_df_tf.head()

C1        C2  cluster
0 -0.434681  0.774386        3
1 -0.112299 -0.096340        0
2 -0.057337 -0.374872        5
3 -0.120687 -0.187576        0
4 -0.191291  0.129232        0

In [257]:
fig = px.scatter(cluster_df_tf, x="C1", y="C2", color="cluster" )
fig.show()

In [258]:
data2.groupby(kmeans_tf.labels_).sum()

profession
0  Employé_de_caisseTéléprospecteur Assistant_pol...
1  Préparateur_de_commandesPréparateur_de_command...
2  CommercialCommercial Chargé_de_clientèleCommer...
3  VendeurVendeur Préparateur_de_commandes Employ...
4  Hôte_d'accueil Gestionnaire_de_stock Agent_de_...
5  CaristePréparateur_de_commandes CaristeCariste...

**Nombre d'experience comme valeur de la matrice**

In [260]:
from scipy.sparse import csr_matrix

In [261]:
sparse_data_m = csr_matrix(data1.pivot(index='worker_id', columns="profession", values='nb_mois_xp').fillna(0))
sparse_data_m.toarray()                         

array([[0., 0., 0., ..., 0., 7., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [262]:
kmeans_m = KMeans(n_clusters=6,random_state=0).fit(sparse_data_m)
pca_m = PCA(n_components=2).fit(sparse_data_m.toarray())
pca_m.explained_variance_ratio_

array([0.0990185 , 0.06927922])

In [263]:
pca_components_m = pca_m.transform(sparse_data_m.toarray())
pca_components_m

array([[ 2.44479969, -0.79006909],
       [-4.47658303, -1.23160063],
       [-4.6773476 ,  1.36295076],
       ...,
       [-3.95704993, -0.60316608],
       [-4.49998918, -1.19817881],
       [-4.50646707, -1.20661595]])

In [264]:
cluster_df_m = pd.DataFrame(pca_components_m, columns=["C1","C2"])
cluster_df_m["cluster"] = kmeans_m.labels_
cluster_df_m.head()

C1        C2  cluster
0  2.444800 -0.790069        0
1 -4.476583 -1.231601        0
2 -4.677348  1.362951        0
3 -5.316888 -6.855455        0
4  7.409443 -0.533127        0

In [265]:
fig = px.scatter(cluster_df_m, x="C1", y="C2", color="cluster" )
fig.show()

In [278]:
data2.groupby(kmeans_m.labels_).sum().profession[5]

"Opérateur_de_fabricationOpérateur_de_fabricationOpérateur_de_fabricationSoudeur Opérateur_de_fabricationOpérateur_de_fabrication Agent_de_conditionnementOpérateur_de_fabricationOpérateur_de_fabricationManutentionnaire Opérateur_de_fabricationCariste Opérateur_de_fabricationOpérateur_de_fabricationOpérateur_de_fabricationOpérateur_de_fabrication PostierOpérateur_de_fabricationOpérateur_de_fabricationCariste Opérateur_de_fabricationOpérateur_de_fabricationOpérateur_de_fabricationManutentionnaire Opérateur_de_fabricationOpérateur_de_fabricationCariste Opérateur_de_fabrication Préparateur_de_commandes Agent_de_conditionnementOpérateur_de_fabrication Contrôleur Ouvrier_TechnicienOpérateur_de_fabricationOpérateur_de_fabricationPréparateur_de_commandes Opérateur_de_fabrication Agent_de_nettoyageOpérateur_de_fabricationOpérateur_de_fabricationOpérateur_de_fabricationPréparateur_de_commandes Opérateur_de_fabricationOpérateur_de_fabricationOpérateur_de_fabricationCommercial Hôtesse Opérateur_de

In [268]:
data2.groupby(kmeans_m.labels_).count()

profession
0       23125
1         305
2         143
3         174
4          90
5          86